In [1]:
import xlsxwriter
import sqlite3
import pandas as pd
import numpy as np
from math import ceil
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
from pprint import pprint

In [2]:
from repytex.tools.evaluation import Evaluation
from repytex.tools.sqlite_getters import all_ev_description

Récupération de la structure du DNB blanc

In [3]:
conn = sqlite3.connect('../recopytex.db')

In [4]:
ev = Evaluation.from_sqlite(21, conn)

In [5]:
ev.ev_df

id        name  term  t_id
0  21  DNB blanc1     2     1

In [6]:
ev.t_df

id name grade
0   1  302    3e

In [7]:
ev.s_df.head()

id              name      surname mail commment  tribe_id
0   1  ABDALLAH ALLAOUI    Taiassima          None         1
1   2             ADANI        Ismou          None         1
2   3           AHAMADA   Dhoulkamal          None         1
3   4           AHAMADI     Asbahati          None         1
4   5   AHAMADI OUSSENI  Ansufiddine          None         1

In [8]:
ev.ex_df

id                     name  eval_id                        date comment
0  64                  1 - QCM       21  2018-02-07 00:00:00.000000        
1  65    2 - Boite de chocolat       21  2018-02-07 00:00:00.000000        
2  66              3 - Scratch       21  2018-02-07 00:00:00.000000        
3  67  4 - Programme de calcul       21  2018-02-07 00:00:00.000000        
4  68              5 - Macaron       21  2018-02-07 00:00:00.000000        
5  69           6 - Inspecteur       21  2018-02-07 00:00:00.000000        
6  70             7 - La tache       21  2018-02-07 00:00:00.000000        
7  91             Présentation       21  2018-02-18 00:00:00.000000

In [9]:
ev.sc_df.head()

Empty DataFrame
Columns: [id, question_id, student_id, value]
Index: []

In [10]:
print(ev.description())

Evaluation DNB blanc1 302 - T2
Ex 1 - QCM
	Qu 1: QCM (2, Cal)
	Qu 2: QCM (2, Cal)
	Qu 3: QCM (2, Cal)
	Qu 4: QCM (2, Rep)
	Qu 5: QCM (2, Cal)
Ex 2 - Boite de chocolat
	Qu 1 à 3: Calcul proba (4, Rep)
	Qu 2: Modification situation (3, Rai)
	Qu 3: Nouvelle composition (3, Rai)
Ex 3 - Scratch
	Qu 1: Que fait le programme (3, Com)
	Qu 2: Réponse à 13 (4, Rai)
	Qu 3: Age pour conduire (3, Cher)
Ex 4 - Programme de calcul
	Qu 1: Application du calcul (5, Cal)
	Qu 2: Renverser le calcul (4, Rai)
	Qu 3: Appliquer à x et developper (6, Cal)
Ex 5 - Macaron
	Qu 1: Proportionnalité (3, Mod)
	Qu 2 et 4: Lecture graphique (4, Rep)
	Qu 3: Écart de température (4, Rep)
	Qu 4: Satisfaction (4, Com)
Ex 6 - Inspecteur
	Qu 1: Hypothèses (2, Cher)
	Qu 1: Reconnaissance des théorèmes (3, Mod)
	Qu 1: Calculs dans les théorèmes (4, Cal)
	Qu 1: Réponse à la question (3, Com)
	Qu 2: Confiance au pilote (3, Rai)
Ex 7 - La tache
	Qu : Décomposition du problème (3, Cher)
	Qu : Lecture des informations (4, Cher)
	Q

## Construction des df à partir du tableur pour les 306

In [11]:
ev_df = ev.ev_df

In [12]:
ex_df = ev.ex_df

In [13]:
q_df = ev.q_df

In [14]:
t_df = ev.t_df

In [15]:
s_df = ev.s_df

Extraction des scores

In [16]:
excelname = './302_dnbblanc1.xls'

In [17]:
xls_df = pd.read_excel(excelname).T

In [18]:
xls_df = xls_df.drop("DNB blanc1", axis = 1)
xls_df.head()

Présentation Ex 1 - QCM 0 - QCM 1 - QCM 2 - QCM 3 - QCM 4 - QCM  \
Competence          NaN        NaN     Cal     Cal     Cal     Rep     Cal   
Barème               10         10       2       2       2       2       2   
ismou                 8          4       2       0       0       0       2   
asbahati             10          6       2       0       2       2       0   
Hadaïta               9          6       0       2       2       2       0   

           Ex 2 - Boite de chocolat 0 - Calcul proba  \
Competence                      NaN              Rep   
Barème                           10                4   
ismou                             0                0   
asbahati                         10                4   
Hadaïta                           7                4   

           1 - Modification situation             ...              \
Competence                        Rai             ...               
Barème                              3             ...               
ismou                               0             ...               
asbahati                            3             ...               
Hadaïta                             3             ...               

           0 - Hypothèses 1 - Reconnaissance des théorèmes  \
Competence           Cher                              Mod   
Barème                  2                                3   
ismou                   0                                1   
asbahati                0                                0   
Hadaïta                 0                                2   

           2 - Calculs dans les théorèmes 3 - Réponse à la question  \
Competence                            Cal                       Com   
Barème                                  4                         3   
ismou                                   0                         0   
asbahati                                0                         0   
Hadaïta                                 0                         1   

           4 - Confiance au pilote Ex 7 - La tache  \
Competence                     Rai             NaN   
Barème                           3              15   
ismou                            0               4   
asbahati                         3              13   
Hadaïta                          3              11   

           0 - Décomposition du problème 1 - Lecture des informations  \
Competence                          Cher                         Cher   
Barème                                 3                            4   
ismou                                  1                            1   
asbahati                               3                            4   
Hadaïta                                3                            4   

           2 - Calculs sensé 3 - Clarté des explications  
Competence               Cal                         Com  
Barème                     4                           4  
ismou                      1                           1  
asbahati                   2                           4  
Hadaïta                    2                           2  

[5 rows x 35 columns]

In [19]:
ex_cols = [c for c in xls_df.columns if 'Ex' in c]
xls_df = xls_df.drop(ex_cols, axis=1)
xls_df.head()

Présentation 0 - QCM 1 - QCM 2 - QCM 3 - QCM 4 - QCM  \
Competence          NaN     Cal     Cal     Cal     Rep     Cal   
Barème               10       2       2       2       2       2   
ismou                 8       2       0       0       0       2   
asbahati             10       2       0       2       2       0   
Hadaïta               9       0       2       2       2       0   

           0 - Calcul proba 1 - Modification situation  \
Competence              Rep                        Rai   
Barème                    4                          3   
ismou                     0                          0   
asbahati                  4                          3   
Hadaïta                   4                          3   

           2 - Nouvelle composition 0 - Que fait le programme  \
Competence                      Rai                       Com   
Barème                            3                         3   
ismou                             0                         2   
asbahati                          3                         3   
Hadaïta                           0                         3   

                       ...             3 - Satisfaction 0 - Hypothèses  \
Competence             ...                          Com           Cher   
Barème                 ...                            4              2   
ismou                  ...                            4              0   
asbahati               ...                            4              0   
Hadaïta                ...                            4              0   

           1 - Reconnaissance des théorèmes 2 - Calculs dans les théorèmes  \
Competence                              Mod                            Cal   
Barème                                    3                              4   
ismou                                     1                              0   
asbahati                                  0                              0   
Hadaïta                                   2                              0   

           3 - Réponse à la question 4 - Confiance au pilote  \
Competence                       Com                     Rai   
Barème                             3                       3   
ismou                              0                       0   
asbahati                           0                       3   
Hadaïta                            1                       3   

           0 - Décomposition du problème 1 - Lecture des informations  \
Competence                          Cher                         Cher   
Barème                                 3                            4   
ismou                                  1                            1   
asbahati                               3                            4   
Hadaïta                                3                            4   

           2 - Calculs sensé 3 - Clarté des explications  
Competence               Cal                         Com  
Barème                     4                           4  
ismou                      1                           1  
asbahati                   2                           4  
Hadaïta                    2                           2  

[5 rows x 28 columns]

In [20]:
q_df

id    name  score_rate  is_leveled  exercise_id competence         domain  \
0  201       1           2           1           64        Cal                  
1  224       2           2           1           64        Cal                  
2  225       3           2           1           64        Cal                  
3  226       4           2           1           64        Rep                  
4  227       5           2           1           64        Cal                  
0  202   1 à 3           4           1           65        Rep          Proba   
1  203       2           3           1           65        Rai          Proba   
2  204       3           3           1           65        Rai          Proba   
0  205       1           3           1           66        Com        Scratch   
1  206       2           4           1           66        Rai        Scratch   
2  207       3           3           1           66       Cher        Scratch   
0  208       1           5           1           67        Cal      Programme   
1  209       2           4           1           67        Rai      Programme   
2  210       3           6           1           67        Cal      Programme   
0  211       1           3           1           68        Mod  Proportionnel   
1  212  2 et 4           4           1           68        Rep      Graphique   
2  213       3           4           1           68        Rep      Graphique   
3  214       4           4           1           68        Com      Graphique   
0  215       1           2           1           69       Cher      Géométrie   
1  216       1           3           1           69        Mod      Géométrie   
2  217       1           4           1           69        Cal      Géométrie   
3  218       1           3           1           69        Com      Géométrie   
4  219       2           3           1           69        Rai      Géométrie   
0  220                   3           1           70       Cher             TC   
1  221                   4           1           70       Cher             TC   
2  222                   4           1           70        Cal             TC   
3  223                   4           1           70        Com             TC   
0  289                  10           1           91        Com   Présentation   

                        comment  
0                           QCM  
1                           QCM  
2                           QCM  
3                           QCM  
4                           QCM  
0                  Calcul proba  
1        Modification situation  
2          Nouvelle composition  
0         Que fait le programme  
1                  Réponse à 13  
2             Age pour conduire  
0         Application du calcul  
1           Renverser le calcul  
2   Appliquer à x et developper  
0              Proportionnalité  
1             Lecture graphique  
2          Écart de température  
3                  Satisfaction  
0                    Hypothèses  
1  Reconnaissance des théorèmes  
2    Calculs dans les théorèmes  
3         Réponse à la question  
4           Confiance au pilote  
0     Décomposition du problème  
1      Lecture des informations  
2                 Calculs sensé  
3       Clarté des explications  
0

In [21]:
q_df

id    name  score_rate  is_leveled  exercise_id competence         domain  \
0  201       1           2           1           64        Cal                  
1  224       2           2           1           64        Cal                  
2  225       3           2           1           64        Cal                  
3  226       4           2           1           64        Rep                  
4  227       5           2           1           64        Cal                  
0  202   1 à 3           4           1           65        Rep          Proba   
1  203       2           3           1           65        Rai          Proba   
2  204       3           3           1           65        Rai          Proba   
0  205       1           3           1           66        Com        Scratch   
1  206       2           4           1           66        Rai        Scratch   
2  207       3           3           1           66       Cher        Scratch   
0  208       1           5           1           67        Cal      Programme   
1  209       2           4           1           67        Rai      Programme   
2  210       3           6           1           67        Cal      Programme   
0  211       1           3           1           68        Mod  Proportionnel   
1  212  2 et 4           4           1           68        Rep      Graphique   
2  213       3           4           1           68        Rep      Graphique   
3  214       4           4           1           68        Com      Graphique   
0  215       1           2           1           69       Cher      Géométrie   
1  216       1           3           1           69        Mod      Géométrie   
2  217       1           4           1           69        Cal      Géométrie   
3  218       1           3           1           69        Com      Géométrie   
4  219       2           3           1           69        Rai      Géométrie   
0  220                   3           1           70       Cher             TC   
1  221                   4           1           70       Cher             TC   
2  222                   4           1           70        Cal             TC   
3  223                   4           1           70        Com             TC   
0  289                  10           1           91        Com   Présentation   

                        comment  
0                           QCM  
1                           QCM  
2                           QCM  
3                           QCM  
4                           QCM  
0                  Calcul proba  
1        Modification situation  
2          Nouvelle composition  
0         Que fait le programme  
1                  Réponse à 13  
2             Age pour conduire  
0         Application du calcul  
1           Renverser le calcul  
2   Appliquer à x et developper  
0              Proportionnalité  
1             Lecture graphique  
2          Écart de température  
3                  Satisfaction  
0                    Hypothèses  
1  Reconnaissance des théorèmes  
2    Calculs dans les théorèmes  
3         Réponse à la question  
4           Confiance au pilote  
0     Décomposition du problème  
1      Lecture des informations  
2                 Calculs sensé  
3       Clarté des explications  
0

In [22]:
cols = {}
qcm = 0
for c in xls_df.columns:
    a = q_df[q_df['comment']==c.split(' - ')[-1]]
    try:
        if "QCM" in c:
            cols[c] = a.id.values[qcm]
            qcm += 1
        else:
            cols[c] = a.id.values[0]
    except IndexError:
        # id de la question de présentation
        cols[c] = 289
cols

{'0 - Application du calcul': 208,
 '0 - Calcul proba': 202,
 '0 - Décomposition du problème': 220,
 '0 - Hypothèses': 215,
 '0 - Proportionnalité': 211,
 '0 - QCM': 201,
 '0 - Que fait le programme': 205,
 '1 - Lecture des informations': 221,
 '1 - Lecture graphique': 212,
 '1 - Modification situation': 203,
 '1 - QCM': 224,
 '1 - Reconnaissance des théorèmes': 216,
 '1 - Renverser le calcul': 209,
 '1 - Réponse à 13': 206,
 '2 - Age pour conduire': 207,
 '2 - Appliquer à x et developper': 210,
 '2 - Calculs dans les théorèmes': 217,
 '2 - Calculs sensé': 222,
 '2 - Nouvelle composition': 204,
 '2 - QCM': 225,
 '2 - Écart de température': 213,
 '3 - Clarté des explications': 223,
 '3 - QCM': 226,
 '3 - Réponse à la question': 218,
 '3 - Satisfaction': 214,
 '4 - Confiance au pilote': 219,
 '4 - QCM': 227,
 'Présentation': 289}

In [23]:
xls_df = xls_df.rename(columns=cols).drop(["Competence", 'Barème', "anchoura"])
xls_df.head()

289 201 224 225 226 227 202 203 204 205 ... 214 215 216 217 218 219  \
ismou      8   2   0   0   0   2   0   0   0   2 ...   4   0   1   0   0   0   
asbahati  10   2   0   2   2   0   4   3   3   3 ...   4   0   0   0   0   3   
Hadaïta    9   0   2   2   2   0   4   3   0   3 ...   4   0   2   0   1   3   
anissa     8   0   2   2   2   2   4   3   2   3 ...   4   0   0   0   0   2   
raydel    10   0   0   2   0   0   4   3   0   3 ...   4   2   2   2   0   3   

         220 221 222 223  
ismou      1   1   1   1  
asbahati   3   4   2   4  
Hadaïta    3   4   2   2  
anissa     3   4   4   4  
raydel     3   4   4   4  

[5 rows x 28 columns]

In [24]:
s_df["surname"]

0                Taiassima
1                    Ismou
2               Dhoulkamal
3                 Asbahati
4              Ansufiddine
5                  Fayadhi
6                  Hadaïta
7                   Anissa
8                   Raydel
9                   Fatima
10                  Elzame
11                  Zalida
12    Abdillah Mze Limassi
13              Zaankidine
14              Kayssoiria
15                    Asna
16                Soibrata
17               Doulkifly
18                  Nassur
19                Anchoura
20                   Nadia
21                    Izak
22                  Bakari
23                Fatoumia
24               Claudiana
25                 Salahou
26              Chaharzade
Name: surname, dtype: object

In [25]:
studs = {}
for s in xls_df.index:
    ss = s_df[s_df['surname'].str.contains(s, case=False)]
    ss = ss.id.values
    try:
        studs[s] = ss[0]
    except IndexError:
        print(f"rien sur {s}")
studs

{'Dhoulkamal': 3,
 'Hadaïta': 7,
 'abdillah mze': 13,
 'anissa': 8,
 'ansufiddine': 5,
 'asbahati': 4,
 'asna': 16,
 'bakari': 23,
 'chaharzade': 76,
 'claudiana': 25,
 'doulkifly': 18,
 'elzame': 11,
 'fatima': 10,
 'fatoumia': 24,
 'fayadhi': 6,
 'ismou': 2,
 'izak': 22,
 'kayssoiria': 15,
 'nadia': 21,
 'nassur': 19,
 'raydel': 9,
 'salahou': 26,
 'soibrata': 17,
 'taiassima': 1,
 'zaankidine': 14,
 'zalida': 12}

In [26]:
xls_df = xls_df.rename(index=studs)
xls_df.head()

289 201 224 225 226 227 202 203 204 205 ... 214 215 216 217 218 219 220 221  \
2   8   2   0   0   0   2   0   0   0   2 ...   4   0   1   0   0   0   1   1   
4  10   2   0   2   2   0   4   3   3   3 ...   4   0   0   0   0   3   3   4   
7   9   0   2   2   2   0   4   3   0   3 ...   4   0   2   0   1   3   3   4   
8   8   0   2   2   2   2   4   3   2   3 ...   4   0   0   0   0   2   3   4   
9  10   0   0   2   0   0   4   3   0   3 ...   4   2   2   2   0   3   3   4   

  222 223  
2   1   1  
4   2   4  
7   2   2  
8   4   4  
9   4   4  

[5 rows x 28 columns]

In [27]:
xls_df = xls_df.stack()
xls_df.head()

2  289    8
   201    2
   224    0
   225    0
   226    0
dtype: object

In [28]:
sc_df = xls_df.reset_index().rename(columns={"level_0": "student_id", "level_1": "question_id", 0:'mark'})
sc_df.head()

student_id  question_id mark
0           2          289    8
1           2          201    2
2           2          224    0
3           2          225    0
4           2          226    0

In [29]:
sc_df["mark"] = sc_df["mark"].astype(int)
sc_df.head()

student_id  question_id  mark
0           2          289     8
1           2          201     2
2           2          224     0
3           2          225     0
4           2          226     0

Maintenant il faut transformer tout ça en niveau de compétence

In [30]:
from repytex.tools.sc_transforms import mark2level
def mark2level_row(x):
    return mark2level(x["mark"], x["score_rate"])

In [31]:
sc_q_df = pd.merge(sc_df, q_df, left_on="question_id", right_on="id")
sc_q_df.head()

student_id  question_id  mark   id name  score_rate  is_leveled  \
0           2          289     8  289               10           1   
1           4          289    10  289               10           1   
2           7          289     9  289               10           1   
3           8          289     8  289               10           1   
4           9          289    10  289               10           1   

   exercise_id competence        domain comment  
0           91        Com  Présentation          
1           91        Com  Présentation          
2           91        Com  Présentation          
3           91        Com  Présentation          
4           91        Com  Présentation

In [32]:
sc_q_df["value"] = sc_q_df.apply(mark2level_row, axis=1)
sc_q_df = sc_q_df[['student_id', 'question_id', 'value']]

In [33]:
sc_df = pd.merge(sc_df, sc_q_df, on=["student_id", 'question_id'])

On met tout ensemble dans l'évaluation

In [34]:
dnbBlanc = Evaluation(ev_df, t_df, s_df, ex_df)
dnbBlanc.set_scores(sc_df)
dnbBlanc.set_ex_qu_structure(ex_df, q_df)
dnbBlanc.set_competence_assessment(sc_df, q_df)


## Exploration

In [35]:
sc_s_df = pd.merge(dnbBlanc.sc_df, dnbBlanc.s_df, left_on='student_id', right_on='id')
sc_s_df = pd.merge(sc_s_df, dnbBlanc.q_df, left_on='question_id', right_on='id')
sc_s_df = pd.merge(sc_s_df, dnbBlanc.ex_df, left_on='exercise_id', right_on='id')
sc_s_df.head()

student_id  question_id  mark  value  id_x      name_x   surname mail  \
0           2          289     8      2     2       ADANI     Ismou        
1           4          289    10      3     4     AHAMADI  Asbahati        
2           7          289     9      3     7  AHMED SAID   Hadaïta        
3           8          289     8      2     8    ALI MADI    Anissa        
4           9          289    10      3     9         ALI    Raydel        

  commment  tribe_id    ...     is_leveled exercise_id  competence  \
0     None         1    ...              1          91         Com   
1     None         1    ...              1          91         Com   
2     None         1    ...              1          91         Com   
3     None         1    ...              1          91         Com   
4     None         1    ...              1          91         Com   

         domain  comment_x  id          name eval_id  \
0  Présentation             91  Présentation      21   
1  Présentation             91  Présentation      21   
2  Présentation             91  Présentation      21   
3  Présentation             91  Présentation      21   
4  Présentation             91  Présentation      21   

                         date comment_y  
0  2018-02-18 00:00:00.000000            
1  2018-02-18 00:00:00.000000            
2  2018-02-18 00:00:00.000000            
3  2018-02-18 00:00:00.000000            
4  2018-02-18 00:00:00.000000            

[5 rows x 23 columns]

Le compte y est! Ouf

In [36]:
sc_s_df.groupby(["surname", "name"]).sum()[["mark", 'score_rate']].head()

mark  score_rate
surname              name                                     
Abdillah Mze Limassi 1 - QCM                     8          10
                     2 - Boite de chocolat       8          10
                     3 - Scratch                10          10
                     4 - Programme de calcul     5          15
                     5 - Macaron                 8          15

In [37]:
sc_s_df.groupby(["surname"]).sum()["mark"].head()

surname
Abdillah Mze Limassi    69
Anissa                  72
Ansufiddine             26
Asbahati                72
Asna                    60
Name: mark, dtype: int64

In [38]:
full_df = pd.merge(dnbBlanc.sc_df, dnbBlanc.s_df, left_on="student_id", right_on="id")
full_df = pd.merge(full_df, dnbBlanc.q_df, left_on="question_id", right_on="id")
full_df.head()

student_id  question_id  mark  value  id_x      name_x   surname mail  \
0           2          289     8      2     2       ADANI     Ismou        
1           4          289    10      3     4     AHAMADI  Asbahati        
2           7          289     9      3     7  AHMED SAID   Hadaïta        
3           8          289     8      2     8    ALI MADI    Anissa        
4           9          289    10      3     9         ALI    Raydel        

  commment  tribe_id  id_y name_y  score_rate  is_leveled  exercise_id  \
0     None         1   289                 10           1           91   
1     None         1   289                 10           1           91   
2     None         1   289                 10           1           91   
3     None         1   289                 10           1           91   
4     None         1   289                 10           1           91   

  competence        domain comment  
0        Com  Présentation          
1        Com  Présentation          
2        Com  Présentation          
3        Com  Présentation          
4        Com  Présentation

## On compile?

In [39]:
from repytex.reports.eval_reports import build_target_name
from repytex.reports.produce_compile import produce_compile

In [40]:
datas = {"evaluation": dnbBlanc}
target = build_target_name('302', 'DNB blanc 1')
target

Path('.//302/report_DNB blanc 1.tex')

In [41]:
template="tpl_reports_eval.tex"

In [42]:
produce_compile(template, datas, target, force=1)

b'! Package Rep Error: Undefinded type of answer: .\n'
b'! Package Rep Error: Undefinded type of answer: .\n'
b'! Package Rep Error: Undefinded type of answer: .\n'
b'! Package Rep Error: Undefinded type of answer: .\n'
b'! Package Rep Error: Undefinded type of answer: .\n'
